In [1]:
from math import asin
from typing import Union
from tqdm import tqdm

import pandas as pd
import numpy as np

from scipy import stats
from statsmodels.stats.meta_analysis import effectsize_smd
from statsmodels.stats import proportion
from statsmodels.stats.power import tt_ind_solve_power
from statsmodels.stats.power import zt_ind_solve_power

In [12]:
def continious_result(control: pd.DataFrame,
                      test: pd.DataFrame,
                      column: str,
                      n_iters: int = 10_000) -> pd.DataFrame:
    # Статистика по выборкам
    size = control.loc[:, column].shape[0]
    
    control_mean = control.loc[:, column].mean()
    test_mean = test.loc[:, column].mean()
    
    control_std = control.loc[:, column].std(ddof=1)
    test_std = test.loc[:, column].std(ddof=1)
    
    # Бутсрап
    booted_diff = []
    for _ in tqdm(range(n_iters)):
        control_sample = control.loc[:, column].sample(n=size, replace=True).values
        test_sample = test.loc[:, column].sample(n=size, replace=True).values
        booted_diff.append(np.mean(control_sample - test_sample))
    
    # Считаем статистику после бустрапа
    md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
    left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
    p_value_ci = 2 * (1 - stats.norm.cdf(np.abs(md_ci / std_ci)))
    
    # Считаем мощность эксперимента
    effect_size, _ = effectsize_smd(mean1=test_mean, sd1=test_std, nobs1=size,
                                    mean2=control_mean, sd2=control_std, nobs2=size)
    power = tt_ind_solve_power(effect_size=effect_size,
                               nobs1=size,
                               alpha=.05,
                               power=None,
                               ratio=1)
    # Формируем отчёт 
    result = pd.DataFrame({'effect_size': effect_size,
                           'alpha': p_value_ci, 
                           'beta': (1-power),
                           'CI': f'[{np.round(left_ci, 3)}, {np.round(right_ci, 3)}]',
                           'difference': md_ci,},
                          index=[column]) 
    return result

In [14]:
def proportion_result(control: pd.DataFrame,
                      test: pd.DataFrame,
                      column: str,
                      n_iters: int = 10_000) -> pd.DataFrame:
    # Вероятность событий
    size = control.loc[:, column].shape[0]
    prop_control = control.loc[:, column].sum() / size
    prop_test = test.loc[:, column].sum() / size
    
    # Бутсрап
    booted_diff = []
    for _ in tqdm(range(n_iters)):
        control_sample = stats.bernoulli.rvs(p=prop_control, size=size)
        test_sample = stats.bernoulli.rvs(p=prop_test, size=size)
        booted_diff.append(np.mean(control_sample - test_sample))
    
    # Считаем статистику после бустрапа
    md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
    left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
    p_value_ci = 2 * (1 - stats.norm.cdf(np.abs(md_ci / std_ci)))
    
    # Считаем мощность эксперимента
    effect_size = proportion.proportion_effectsize(prop_control, prop_test)
    power = zt_ind_solve_power(effect_size=effect_size,
                               nobs1=size,
                               alpha=.05,
                               power=None,
                               ratio=1)
    # Формируем отчёт 
    result = pd.DataFrame({'effect_size': effect_size,
                           'alpha': p_value_ci, 
                           'beta': (1-power),
                           'CI': f'[{np.round(left_ci, 3)}, {np.round(right_ci, 3)}]',
                           'difference': md_ci,},
                          index=[column]) 
    return result

**Проанализируйте результаты эксперимента и напишите свои рекомендации менеджеру.**

In [15]:
data = pd.read_csv('gb_sem_9_hw.csv')
data

userid  version  sum_gamerounds  retention_1  retention_7
0          116  gate_30               3        False        False
1          337  gate_30              38         True        False
2          377  gate_40             165         True        False
3          483  gate_40               1        False        False
4          488  gate_40             179         True         True
...        ...      ...             ...          ...          ...
90184  9999441  gate_40              97         True        False
90185  9999479  gate_40              30        False        False
90186  9999710  gate_30              28         True        False
90187  9999768  gate_40              51         True        False
90188  9999861  gate_40              16        False        False

[90189 rows x 5 columns]

In [4]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 90189 entries, 0 to 90188
Data columns (total 5 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   userid          90189 non-null  int64 
 1   version         90189 non-null  object
 2   sum_gamerounds  90189 non-null  int64 
 3   retention_1     90189 non-null  bool  
 4   retention_7     90189 non-null  bool  
dtypes: bool(2), int64(2), object(1)
memory usage: 2.2+ MB


In [5]:
data.shape

(90189, 5)

In [6]:
data.describe()

userid  sum_gamerounds
count  9.018900e+04    90189.000000
mean   4.998412e+06       51.872457
std    2.883286e+06      195.050858
min    1.160000e+02        0.000000
25%    2.512230e+06        5.000000
50%    4.995815e+06       16.000000
75%    7.496452e+06       51.000000
max    9.999861e+06    49854.000000

Смотрим на группы по отдельности.

In [64]:
data.groupby('version')['sum_gamerounds'].describe()

count       mean         std  min  25%   50%   75%      max
version                                                               
gate_30  44700.0  52.456264  256.716423  0.0  5.0  17.0  50.0  49854.0
gate_40  45489.0  51.298776  103.294416  0.0  5.0  16.0  52.0   2640.0

In [65]:
data.userid.nunique()

90189

Повторяющихся пользователей нет.
Строим гистограмму.

In [62]:
import plotly.express as px
fig = px.histogram(data,
                   x='sum_gamerounds',
                   color = 'version',
                   title='Игровые раунды',
                   marginal = 'box',
                   nbins = 100,
                   barmode='overlay')

fig.show()

sum_gamerounds является непрерывной метрикой. Имеет эспоненциальное распределение.

In [49]:
continious_result(control, test, column='sum_gamerounds')

100%|██████████| 10000/10000 [00:29<00:00, 333.75it/s]


effect_size     alpha      beta              CI  difference
sum_gamerounds    -0.005915  0.381447  0.856725  [-0.977, 4.09]    1.154526

Вывод: так как доверительный интервал включает в себя 0, альфа > 0,05,  бетта очень большая 85 можем сказать что результат не статистически значим.

In [30]:
# fig = px.histogram(data[data['retention_1'] == 1],
#                    x='sum_gamerounds',
#                    color = 'version',
#                    title='retention_1',
#                    marginal = 'box',
#                    nbins = 200)
# fig.show()

In [43]:
# fig = px.histogram(data[data['retention_7'] == 1],
#                    x='sum_gamerounds',
#                    color = 'version',
#                    title='retention_7',
#                    marginal = 'box',
#                    nbins = 10000)
# fig.show()

retention_1 и retention_7 являются качественными метриками.

In [55]:
fig = px.histogram(data, x='retention_1',
                   color = 'version',barmode='group',
                   height=400)
fig.show()

In [56]:
proportion_result(control, test, column='retention_1')

100%|██████████| 10000/10000 [00:28<00:00, 353.98it/s]


effect_size    alpha      beta               CI  difference
retention_1    -0.003823  0.55559  0.911819  [-0.009, 0.004]   -0.001969

Так же видим что 0 входит в доверительный интервал, альфа больше 0,05, и бетта огромная 91. Статистической заначимости нет.

In [57]:
fig = px.histogram(data, x='retention_7',
                   color = 'version',barmode='group',
                   height=400)
fig.show()

In [58]:
proportion_result(control, test, column='retention_7')

100%|██████████| 10000/10000 [00:22<00:00, 438.70it/s]


effect_size     alpha      beta            CI  difference
retention_7     0.012776  0.056281  0.519844  [-0.0, 0.01]    0.004971

Такой же результат видим и у retention_7.


**Заключительный вывод: Исследовав три метрики, мы определили что Статистической разницы между version gate_30 и version gate_40 НЕТ!**